In [2]:
import re
import numpy as np
import pandas as pd
from pprint import pprint
import nltk

# Gensim
import gensim as gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from nltk.stem import WordNetLemmatizer, SnowballStemmer
from nltk.stem.porter import *
import numpy as np

# spacy for lemmatization
import spacy

# Plotting tools
import pyLDAvis
import pyLDAvis.gensim  
import matplotlib.pyplot as plt
%matplotlib inline

# Enable logging for gensim - optional
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)

import warnings
warnings.filterwarnings("ignore",category=DeprecationWarning)

In [5]:
list_books = ['The-Economist-USA.txt','The_Descent_of_Man.txt',
             'The First Men In The Moon.txt','The Evolution of Man.txt',
             'Problems of Genetics.txt','Islands of Space.txt'
              ]
file = [open(book,'r',encoding="utf8") for book in list_books]

file_text = [fil.read() for fil in file]
df_text = pd.DataFrame(file_text)
df_text['index'] = df_text.index
documents = df_text
for fil in file:
    fil.close()

In [6]:
documents.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6 entries, 0 to 5
Data columns (total 2 columns):
0        6 non-null object
index    6 non-null int64
dtypes: int64(1), object(1)
memory usage: 176.0+ bytes


In [7]:
np.random.seed(2019)

In [8]:
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\SK\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [9]:
stemmer = SnowballStemmer('english')

def lemmatize_stemming(text):
    return stemmer.stem(WordNetLemmatizer().lemmatize(text, pos='v'))

def preprocess(text):
    result = []
    for token in gensim.utils.simple_preprocess(text):
        if token not in gensim.parsing.preprocessing.STOPWORDS and len(token) > 3:
            result.append(lemmatize_stemming(token))
    return result

In [10]:
doc_sample = documents[documents['index'] == 1].values[0][0]

print('original document: ')
words = []
for word in doc_sample.split(' '):
    words.append(word)
print(words)

original document: 


['\ufeffThe', 'Project', 'Gutenberg', 'EBook', 'of', 'The', 'Descent', 'of', 'Man,', 'by', 'Charles', 'Darwin\n\nThis', 'eBook', 'is', 'for', 'the', 'use', 'of', 'anyone', 'anywhere', 'at', 'no', 'cost', 'and', 'with', 'almost\nno', 'restrictions', 'whatsoever.', 'You', 'may', 'copy', 'it,', 'give', 'it', 'away', 'or', 're-use\nit', 'under', 'the', 'terms', 'of', 'the', 'Project', 'Gutenberg', 'License', 'included', 'with', 'this\neBook', 'or', 'online', 'at', 'www.gutenberg.org\n\n\nTitle:', 'The', 'Descent', 'of', 'Man\n\nAuthor:', 'Charles', 'Darwin\n\nPosting', 'Date:', 'January', '6,', '2013', '[EBook', '#2300]\nFirst', 'Posted:', 'November', '28,', '1999\nLast', 'Updated:', 'October', '9,', '2017\n\nLanguage:', 'English\n\n\n***', 'START', 'OF', 'THIS', 'PROJECT', 'GUTENBERG', 'EBOOK', 'THE', 'DESCENT', 'OF', 'MAN', '***\n\n\n\n\nProduced', 'by', 'Sue', 'Asscher\n\n\n\n\n\n\n\n\n\n\nTHE', 'DESCENT', 'OF', 'MAN\n\nAND\n\nSELECTION', 'IN', 'RELATION', 'TO', 'SEX\n\n\nWorks', 'by', 

In [11]:
print('\n\n tokenized and lemmatized document: ')
print(preprocess(doc_sample))



 tokenized and lemmatized document: 


['project', 'gutenberg', 'ebook', 'descent', 'charl', 'darwin', 'ebook', 'cost', 'restrict', 'whatsoev', 'copi', 'away', 'term', 'project', 'gutenberg', 'licens', 'includ', 'ebook', 'onlin', 'gutenberg', 'titl', 'descent', 'author', 'charl', 'darwin', 'post', 'date', 'januari', 'ebook', 'post', 'novemb', 'updat', 'octob', 'languag', 'english', 'start', 'project', 'gutenberg', 'ebook', 'descent', 'produc', 'asscher', 'descent', 'select', 'relat', 'work', 'charl', 'darwin', 'life', 'letter', 'charl', 'darwin', 'chapter', 'edit', 'franci', 'darwin', 'portrait', 'volum', 'popular', 'edit', 'condens', 'volum', 'naturalist', 'journal', 'research', 'natur', 'histori', 'geolog', 'countri', 'visit', 'voyag', 'round', 'world', 'illustr', 'pritchett', 'popular', 'edit', 'woodcut', 'cheaper', 'edit', 'origin', 'speci', 'mean', 'natur', 'select', 'preserv', 'favour', 'race', 'struggl', 'life', 'larg', 'type', 'edit', 'volum', 'popular', 'edit', 'cheaper', 'edit', 'portrait', 'contriv', 'orchid', 'f

In [12]:
processed_docs = documents[0].map(preprocess)

In [13]:
processed_docs[:5]

0    [come, brexit, elect, german, reunif, save, pe...
1    [project, gutenberg, ebook, descent, charl, da...
2    [project, gutenberg, ebook, moon, well, ebook,...
3    [project, gutenberg, ebook, evolut, ernst, hae...
4    [project, gutenberg, ebook, problem, genet, wi...
Name: 0, dtype: object

In [14]:
dictionary = gensim.corpora.Dictionary(processed_docs)

In [15]:
count = 0
for k, v in dictionary.iteritems():
    print(k, v)
    count += 1
    if count > 10:
        break

0 ababa
1 abandon
2 abat
3 abattoir
4 abaya
5 abbasid
6 abbey
7 abduct
8 abdul
9 abdulmahdi
10 abil


In [69]:
# dictionary.filter_extremes(no_below=15, no_above=0.5, keep_n=100000)

In [16]:
bow_corpus = [dictionary.doc2bow(doc) for doc in processed_docs]
print(len(bow_corpus))
bow_corpus[1]

6


[(1, 1),
 (10, 7),
 (12, 83),
 (13, 2),
 (15, 26),
 (17, 2),
 (18, 5),
 (21, 2),
 (22, 76),
 (23, 30),
 (24, 7),
 (25, 4),
 (26, 2),
 (27, 10),
 (30, 12),
 (32, 2),
 (34, 45),
 (35, 14),
 (36, 8),
 (37, 13),
 (39, 15),
 (41, 193),
 (42, 163),
 (43, 1),
 (44, 3),
 (46, 7),
 (48, 1),
 (49, 312),
 (50, 11),
 (53, 53),
 (54, 159),
 (55, 39),
 (58, 1),
 (59, 54),
 (60, 8),
 (61, 8),
 (63, 58),
 (64, 63),
 (66, 40),
 (67, 10),
 (76, 105),
 (77, 3),
 (78, 127),
 (80, 10),
 (83, 259),
 (86, 80),
 (87, 91),
 (88, 3),
 (89, 4),
 (92, 2),
 (93, 3),
 (95, 4),
 (97, 14),
 (98, 46),
 (99, 1),
 (100, 2),
 (101, 101),
 (102, 49),
 (103, 1),
 (104, 56),
 (105, 32),
 (107, 5),
 (110, 3),
 (111, 7),
 (113, 33),
 (114, 28),
 (116, 1),
 (120, 28),
 (121, 1),
 (132, 7),
 (141, 1),
 (142, 6),
 (145, 2),
 (151, 1),
 (152, 6),
 (153, 56),
 (154, 10),
 (163, 124),
 (164, 4),
 (165, 5),
 (167, 17),
 (174, 23),
 (175, 9),
 (178, 21),
 (182, 13),
 (183, 2),
 (184, 1),
 (191, 118),
 (192, 154),
 (196, 1),
 (198, 4)

In [17]:
bow_doc_1 = bow_corpus[1]

for i in range(len(bow_doc_1)):
    print("Word {} (\"{}\") appears {} time.".format(bow_doc_1[i][0], 
                                                     dictionary[bow_doc_1[i][0]], 
                                                     bow_doc_1[i][1]))

Word 1 ("abandon") appears 1 time.
Word 10 ("abil") appears 7 time.
Word 12 ("abl") appears 83 time.
Word 13 ("abli") appears 2 time.
Word 15 ("abnorm") appears 26 time.
Word 17 ("abolish") appears 2 time.
Word 18 ("abort") appears 5 time.
Word 21 ("abroad") appears 2 time.
Word 22 ("absenc") appears 76 time.
Word 23 ("absolut") appears 30 time.
Word 24 ("absorb") appears 7 time.
Word 25 ("absorpt") appears 4 time.
Word 26 ("absurd") appears 2 time.
Word 27 ("abund") appears 10 time.
Word 30 ("academi") appears 12 time.
Word 32 ("acceler") appears 2 time.
Word 34 ("accept") appears 45 time.
Word 35 ("access") appears 14 time.
Word 36 ("accid") appears 8 time.
Word 37 ("accident") appears 13 time.
Word 39 ("accompani") appears 15 time.
Word 41 ("accord") appears 193 time.
Word 42 ("account") appears 163 time.
Word 43 ("accru") appears 1 time.
Word 44 ("accus") appears 3 time.
Word 46 ("acknowledg") appears 7 time.
Word 48 ("acquiesc") appears 1 time.
Word 49 ("acquir") appears 312 time.

Word 517 ("believ") appears 198 time.
Word 520 ("belong") appears 114 time.
Word 521 ("belov") appears 5 time.
Word 522 ("belt") appears 17 time.
Word 524 ("bend") appears 11 time.
Word 525 ("beneath") appears 21 time.
Word 531 ("bennett") appears 5 time.
Word 536 ("berlin") appears 1 time.
Word 540 ("berri") appears 1 time.
Word 543 ("best") appears 104 time.
Word 545 ("betray") appears 6 time.
Word 546 ("better") appears 58 time.
Word 547 ("bewild") appears 1 time.
Word 550 ("bias") appears 1 time.
Word 558 ("bilater") appears 1 time.
Word 561 ("bill") appears 6 time.
Word 564 ("bind") appears 8 time.
Word 568 ("biograph") appears 1 time.
Word 569 ("biographi") appears 28 time.
Word 570 ("biolog") appears 1 time.
Word 572 ("bird") appears 1103 time.
Word 573 ("birmingham") appears 1 time.
Word 574 ("birth") appears 108 time.
Word 576 ("birthplac") appears 10 time.
Word 579 ("bishop") appears 12 time.
Word 582 ("bit") appears 3 time.
Word 584 ("black") appears 272 time.
Word 586 ("bla

Word 1066 ("column") appears 7 time.
Word 1069 ("combat") appears 12 time.
Word 1070 ("combin") appears 15 time.
Word 1071 ("come") appears 140 time.
Word 1073 ("comfort") appears 7 time.
Word 1074 ("command") appears 11 time.
Word 1077 ("comment") appears 5 time.
Word 1080 ("commerci") appears 1 time.
Word 1081 ("commiss") appears 1 time.
Word 1083 ("commit") appears 5 time.
Word 1086 ("common") appears 298 time.
Word 1088 ("communal") appears 12 time.
Word 1089 ("communic") appears 18 time.
Word 1091 ("communism") appears 1 time.
Word 1092 ("communist") appears 1 time.
Word 1094 ("communiti") appears 48 time.
Word 1096 ("comp") appears 4 time.
Word 1097 ("compani") appears 4 time.
Word 1098 ("companion") appears 13 time.
Word 1099 ("compar") appears 109 time.
Word 1100 ("comparison") appears 45 time.
Word 1102 ("compel") appears 20 time.
Word 1103 ("compens") appears 10 time.
Word 1104 ("compet") appears 11 time.
Word 1105 ("competit") appears 10 time.
Word 1106 ("compil") appears 2 

Word 1493 ("despis") appears 1 time.
Word 1494 ("despit") appears 1 time.
Word 1495 ("destin") appears 1 time.
Word 1496 ("destini") appears 1 time.
Word 1497 ("destroy") appears 31 time.
Word 1498 ("destruct") appears 26 time.
Word 1499 ("detail") appears 27 time.
Word 1500 ("detain") appears 1 time.
Word 1501 ("detect") appears 23 time.
Word 1504 ("deterior") appears 7 time.
Word 1505 ("determin") appears 50 time.
Word 1513 ("develop") appears 608 time.
Word 1515 ("devoid") appears 1 time.
Word 1516 ("devot") appears 11 time.
Word 1527 ("dictat") appears 1 time.
Word 1530 ("die") appears 20 time.
Word 1532 ("diet") appears 4 time.
Word 1533 ("differ") appears 1408 time.
Word 1535 ("digit") appears 15 time.
Word 1536 ("digniti") appears 4 time.
Word 1540 ("diminish") appears 13 time.
Word 1541 ("diminut") appears 13 time.
Word 1546 ("direct") appears 143 time.
Word 1547 ("director") appears 3 time.
Word 1548 ("dirt") appears 2 time.
Word 1549 ("dirti") appears 2 time.
Word 1551 ("disa

Word 1953 ("expans") appears 7 time.
Word 1954 ("expect") appears 35 time.
Word 1955 ("expedit") appears 6 time.
Word 1956 ("expel") appears 7 time.
Word 1957 ("expenditur") appears 2 time.
Word 1958 ("expens") appears 6 time.
Word 1959 ("experi") appears 72 time.
Word 1961 ("expert") appears 1 time.
Word 1964 ("explain") appears 51 time.
Word 1965 ("explan") appears 41 time.
Word 1969 ("explor") appears 2 time.
Word 1973 ("export") appears 1 time.
Word 1974 ("expos") appears 75 time.
Word 1975 ("exposur") appears 13 time.
Word 1976 ("express") appears 82 time.
Word 1978 ("extend") appears 49 time.
Word 1979 ("extens") appears 12 time.
Word 1980 ("extent") appears 58 time.
Word 1981 ("extern") appears 43 time.
Word 1982 ("extinct") appears 56 time.
Word 1983 ("extort") appears 1 time.
Word 1984 ("extra") appears 1 time.
Word 1985 ("extract") appears 14 time.
Word 1987 ("extraordinari") appears 61 time.
Word 1988 ("extraordinarili") appears 7 time.
Word 1990 ("extravag") appears 6 time.

...

Word 10262 ("paddl") appears 4 time.
Word 10263 ("padova") appears 1 time.
Word 10264 ("pagan") appears 1 time.
Word 10265 ("paget") appears 4 time.
Word 10266 ("pagurus") appears 4 time.
Word 10267 ("palaemon") appears 2 time.
Word 10268 ("palaeont") appears 1 time.
Word 10269 ("palaeontolog") appears 1 time.
Word 10270 ("palaeorni") appears 10 time.
Word 10271 ("palamedea") appears 6 time.
Word 10272 ("palat") appears 4 time.
Word 10273 ("pale") appears 36 time.
Word 10274 ("paleolith") appears 2 time.
Word 10275 ("paler") appears 14 time.
Word 10276 ("palestin") appears 6 time.
Word 10277 ("palla") appears 16 time.
Word 10278 ("pallasian") appears 1 time.
Word 10279 ("palm") appears 5 time.
Word 10280 ("palmari") appears 3 time.
Word 10281 ("palmat") appears 1 time.
Word 10282 ("palmata") appears 2 time.
Word 10283 ("palmip") appears 2 time.
Word 10284 ("palpit") appears 1 time.
Word 10285 ("paludosus") appears 4 time.
Word 10286 ("pampa") appears 5 time.
Word 10287 ("pamper") appea

Word 10468 ("phys") appears 17 time.
Word 10469 ("physic") appears 31 time.
Word 10470 ("physician") appears 1 time.
Word 10471 ("physiognomi") appears 5 time.
Word 10472 ("physiolog") appears 30 time.
Word 10473 ("physiologist") appears 1 time.
Word 10474 ("pica") appears 2 time.
Word 10475 ("picide") appears 1 time.
Word 10476 ("pickard") appears 1 time.
Word 10477 ("picker") appears 2 time.
Word 10478 ("picta") appears 10 time.
Word 10479 ("picton") appears 2 time.
Word 10480 ("pictori") appears 1 time.
Word 10481 ("picu") appears 1 time.
Word 10482 ("picus") appears 4 time.
Word 10483 ("pie") appears 11 time.
Word 10484 ("piebald") appears 7 time.
Word 10485 ("pierc") appears 12 time.
Word 10486 ("pieri") appears 5 time.
Word 10487 ("pierr") appears 2 time.
Word 10488 ("pig") appears 15 time.
Word 10489 ("pigeon") appears 84 time.
Word 10490 ("pike") appears 15 time.
Word 10491 ("pillar") appears 2 time.
Word 10492 ("pimelia") appears 3 time.
Word 10493 ("pin") appears 3 time.
Word

Word 10675 ("probosci") appears 4 time.
Word 10676 ("proboscideus") appears 2 time.
Word 10677 ("proc") appears 54 time.
Word 10678 ("procced") appears 1 time.
Word 10679 ("procreat") appears 4 time.
Word 10680 ("proctotretus") appears 5 time.
Word 10681 ("procur") appears 18 time.
Word 10682 ("prodigi") appears 9 time.
Word 10683 ("produir") appears 1 time.
Word 10684 ("prof") appears 148 time.
Word 10685 ("profess") appears 1 time.
Word 10686 ("profici") appears 2 time.
Word 10687 ("profil") appears 1 time.
Word 10688 ("profit") appears 11 time.
Word 10689 ("proflig") appears 8 time.
Word 10690 ("profligaci") appears 8 time.
Word 10691 ("profond") appears 1 time.
Word 10692 ("progenitor") appears 145 time.
Word 10693 ("progn") appears 5 time.
Word 10694 ("prognath") appears 3 time.
Word 10695 ("prohibit") appears 1 time.
Word 10696 ("prolif") appears 5 time.
Word 10697 ("pronounc") appears 20 time.
Word 10698 ("pronuba") appears 1 time.
Word 10699 ("pronunci") appears 1 time.
Word 10

Word 10884 ("reflect") appears 31 time.
Word 10885 ("reflex") appears 3 time.
Word 10886 ("refug") appears 3 time.
Word 10887 ("refund") appears 10 time.
Word 10888 ("refut") appears 1 time.
Word 10889 ("regal") appears 3 time.
Word 10890 ("regener") appears 2 time.
Word 10891 ("regent") appears 4 time.
Word 10892 ("regiment") appears 4 time.
Word 10893 ("registrar") appears 3 time.
Word 10894 ("regn") appears 4 time.
Word 10895 ("regrowth") appears 2 time.
Word 10896 ("rehears") appears 1 time.
Word 10897 ("reichert") appears 1 time.
Word 10898 ("reign") appears 3 time.
Word 10899 ("reindeer") appears 27 time.
Word 10900 ("reintroduc") appears 1 time.
Word 10901 ("reis") appears 6 time.
Word 10902 ("reiter") appears 3 time.
Word 10903 ("rejoic") appears 1 time.
Word 10904 ("rejoind") appears 1 time.
Word 10905 ("relativ") appears 1 time.
Word 10906 ("relic") appears 3 time.
Word 10907 ("remaind") appears 2 time.
Word 10908 ("remarqu") appears 1 time.
Word 10909 ("remembr") appears 1 t

Word 11095 ("saturniida") appears 4 time.
Word 11096 ("saurait") appears 1 time.
Word 11097 ("sauratus") appears 1 time.
Word 11098 ("savag") appears 247 time.
Word 11099 ("savageri") appears 1 time.
Word 11100 ("savill") appears 1 time.
Word 11101 ("saviotti") appears 2 time.
Word 11102 ("saxicola") appears 3 time.
Word 11103 ("saxon") appears 6 time.
Word 11104 ("scabi") appears 1 time.
Word 11105 ("scallop") appears 1 time.
Word 11106 ("scan") appears 1 time.
Word 11107 ("scandalis") appears 1 time.
Word 11108 ("scandinavia") appears 7 time.
Word 11109 ("scandinavian") appears 2 time.
Word 11110 ("scanti") appears 5 time.
Word 11111 ("scantili") appears 1 time.
Word 11112 ("scapula") appears 1 time.
Word 11113 ("scapular") appears 2 time.
Word 11114 ("scapulatus") appears 2 time.
Word 11115 ("scar") appears 7 time.
Word 11116 ("scarc") appears 18 time.
Word 11117 ("scarciti") appears 5 time.
Word 11118 ("scarlet") appears 16 time.
Word 11119 ("scatter") appears 5 time.
Word 11120 ("

In [18]:
from gensim import corpora, models

tfidf = models.TfidfModel(bow_corpus)

In [19]:
corpus_tfidf = tfidf[bow_corpus]

In [20]:
from pprint import pprint

for doc in corpus_tfidf:
    pprint(doc)
    break

[(0, 0.014342104054779061),
 (1, 0.0008756336273511451),
 (2, 0.0017587641679075762),
 (3, 0.0017587641679075762),
 (4, 0.002868420810955812),
 (5, 0.005736841621911624),
 (6, 0.002868420810955812),
 (7, 0.002868420810955812),
 (8, 0.005736841621911624),
 (9, 0.002868420810955812),
 (10, 0.007767596501337654),
 (11, 0.028684208109558122),
 (12, 0.0023350230062697203),
 (13, 0.0017587641679075762),
 (14, 0.002868420810955812),
 (15, 0.0006491075248593397),
 (16, 0.0017587641679075762),
 (17, 0.005276292503722729),
 (18, 0.007767596501337654),
 (19, 0.002868420810955812),
 (20, 0.005736841621911624),
 (21, 0.006657939858289418),
 (22, 0.00029187787578371504),
 (23, 0.0008756336273511451),
 (24, 0.0011675115031348601),
 (25, 0.0006491075248593397),
 (26, 0.0006491075248593397),
 (27, 0.0032455376242966983),
 (28, 0.017210524865734874),
 (29, 0.022947366487646496),
 (30, 0.003328969929144709),
 (31, 0.002868420810955812),
 (32, 0.0017512672547022902),
 (33, 0.002868420810955812),
 (35, 0.0

 (288, 0.002868420810955812),
 (289, 0.002868420810955812),
 (290, 0.057368416219116244),
 (291, 0.002868420810955812),
 (292, 0.005837557515674301),
 (293, 0.003210656633620865),
 (294, 0.0006491075248593397),
 (296, 0.002868420810955812),
 (297, 0.0011096566430482363),
 (298, 0.002868420810955812),
 (299, 0.0017587641679075762),
 (300, 0.00408629026097201),
 (301, 0.0017587641679075762),
 (302, 0.020078945676690687),
 (303, 0.016644849645723544),
 (304, 0.002868420810955812),
 (305, 0.002868420810955812),
 (306, 0.0011096566430482363),
 (308, 0.00029187787578371504),
 (309, 0.0008756336273511451),
 (310, 0.005192860198874718),
 (311, 0.0011096566430482363),
 (312, 0.008605262432867437),
 (313, 0.005548283215241182),
 (314, 0.002868420810955812),
 (315, 0.002868420810955812),
 (316, 0.013315879716578835),
 (317, 0.007789290298312076),
 (318, 0.011473683243823248),
 (319, 0.002868420810955812),
 (320, 0.002868420810955812),
 (321, 0.0012982150497186794),
 (322, 0.0006491075248593397),


 (565, 0.014342104054779061),
 (566, 0.002868420810955812),
 (567, 0.002868420810955812),
 (568, 0.0017587641679075762),
 (569, 0.0017587641679075762),
 (570, 0.002596430099437359),
 (571, 0.0011096566430482363),
 (572, 0.0008756336273511451),
 (573, 0.0022193132860964726),
 (574, 0.0029187787578371506),
 (575, 0.002868420810955812),
 (576, 0.0017587641679075762),
 (577, 0.002868420810955812),
 (578, 0.002868420810955812),
 (579, 0.0022193132860964726),
 (580, 0.020078945676690687),
 (581, 0.002868420810955812),
 (582, 0.0035175283358151524),
 (583, 0.002868420810955812),
 (584, 0.00408629026097201),
 (585, 0.002868420810955812),
 (586, 0.005276292503722729),
 (587, 0.003210656633620865),
 (588, 0.002868420810955812),
 (589, 0.0017587641679075762),
 (590, 0.0012982150497186794),
 (591, 0.0006491075248593397),
 (592, 0.0022193132860964726),
 (593, 0.0006491075248593397),
 (594, 0.0017587641679075762),
 (595, 0.0014593893789185753),
 (596, 0.002868420810955812),
 (597, 0.0028684208109558

 (837, 0.002868420810955812),
 (838, 0.0022193132860964726),
 (839, 0.0029187787578371506),
 (840, 0.0011096566430482363),
 (841, 0.0011096566430482363),
 (842, 0.002868420810955812),
 (843, 0.002868420810955812),
 (844, 0.0017587641679075762),
 (845, 0.002868420810955812),
 (846, 0.002868420810955812),
 (848, 0.05803921754095001),
 (849, 0.005736841621911624),
 (850, 0.002043145130486005),
 (851, 0.0035175283358151524),
 (852, 0.0023350230062697203),
 (853, 0.002868420810955812),
 (854, 0.0011096566430482363),
 (855, 0.005736841621911624),
 (856, 0.007035056671630305),
 (857, 0.003328969929144709),
 (859, 0.0035175283358151524),
 (860, 0.00029187787578371504),
 (861, 0.002868420810955812),
 (862, 0.0005837557515674301),
 (863, 0.011473683243823248),
 (864, 0.002868420810955812),
 (865, 0.004438626572192945),
 (866, 0.003210656633620865),
 (867, 0.0011675115031348601),
 (868, 0.011473683243823248),
 (869, 0.011473683243823248),
 (870, 0.005736841621911624),
 (871, 0.005276292503722729)

 (1114, 0.0011096566430482363),
 (1115, 0.0022193132860964726),
 (1116, 0.0014593893789185753),
 (1117, 0.004438626572192945),
 (1118, 0.0011096566430482363),
 (1119, 0.0006491075248593397),
 (1120, 0.0017587641679075762),
 (1121, 0.004543752674015378),
 (1123, 0.0017587641679075762),
 (1124, 0.0035175283358151524),
 (1125, 0.004438626572192945),
 (1126, 0.0005837557515674301),
 (1127, 0.00029187787578371504),
 (1128, 0.004378168136755726),
 (1129, 0.0017587641679075762),
 (1130, 0.0035175283358151524),
 (1131, 0.002868420810955812),
 (1132, 0.002868420810955812),
 (1133, 0.0014593893789185753),
 (1134, 0.0011675115031348601),
 (1135, 0.02108347621791649),
 (1136, 0.0017587641679075762),
 (1137, 0.002868420810955812),
 (1138, 0.004378168136755726),
 (1139, 0.003210656633620865),
 (1140, 0.0012982150497186794),
 (1141, 0.0005837557515674301),
 (1142, 0.0011096566430482363),
 (1143, 0.002868420810955812),
 (1144, 0.002043145130486005),
 (1145, 0.005736841621911624),
 (1146, 0.00286842081

...

 (2484, 0.005736841621911624),
 (2486, 0.0017587641679075762),
 (2487, 0.0006491075248593397),
 (2488, 0.002868420810955812),
 (2489, 0.002868420810955812),
 (2490, 0.017210524865734874),
 (2491, 0.0035175283358151524),
 (2492, 0.002868420810955812),
 (2493, 0.0017587641679075762),
 (2494, 0.0017587641679075762),
 (2495, 0.002868420810955812),
 (2496, 0.0005837557515674301),
 (2497, 0.002868420810955812),
 (2498, 0.002868420810955812),
 (2499, 0.005736841621911624),
 (2500, 0.002043145130486005),
 (2501, 0.002868420810955812),
 (2502, 0.009923847776646311),
 (2503, 0.007005069018809161),
 (2504, 0.005192860198874718),
 (2505, 0.008605262432867437),
 (2506, 0.005736841621911624),
 (2507, 0.002868420810955812),
 (2508, 0.0005837557515674301),
 (2509, 0.005736841621911624),
 (2510, 0.002868420810955812),
 (2511, 0.0006491075248593397),
 (2512, 0.005736841621911624),
 (2513, 0.002868420810955812),
 (2514, 0.0035175283358151524),
 (2515, 0.0012982150497186794),
 (2516, 0.00887725314438589),

 (2760, 0.0022193132860964726),
 (2761, 0.002868420810955812),
 (2763, 0.001947322574578019),
 (2764, 0.008605262432867437),
 (2765, 0.0012982150497186794),
 (2766, 0.005276292503722729),
 (2768, 0.005276292503722729),
 (2769, 0.0005837557515674301),
 (2770, 0.002868420810955812),
 (2771, 0.0011096566430482363),
 (2772, 0.002868420810955812),
 (2773, 0.0005837557515674301),
 (2774, 0.001947322574578019),
 (2775, 0.002868420810955812),
 (2776, 0.0035175283358151524),
 (2777, 0.0017587641679075762),
 (2778, 0.0017587641679075762),
 (2779, 0.002868420810955812),
 (2780, 0.002868420810955812),
 (2781, 0.004438626572192945),
 (2782, 0.0032455376242966983),
 (2783, 0.002868420810955812),
 (2784, 0.002868420810955812),
 (2785, 0.008793820839537881),
 (2786, 0.0006491075248593397),
 (2787, 0.003328969929144709),
 (2788, 0.0023350230062697203),
 (2789, 0.0017587641679075762),
 (2790, 0.0012982150497186794),
 (2791, 0.0006491075248593397),
 (2792, 0.05326351886631534),
 (2793, 0.0055456796398905

 (5631, 0.002868420810955812),
 (5632, 0.005736841621911624),
 (5633, 0.0035175283358151524),
 (5634, 0.0017587641679075762),
 (5635, 0.002868420810955812),
 (5636, 0.0035025345094045804),
 (5637, 0.002868420810955812),
 (5638, 0.003328969929144709),
 (5639, 0.16349998622448128),
 (5640, 0.002868420810955812),
 (5641, 0.002868420810955812),
 (5642, 0.0023350230062697203),
 (5643, 0.0017587641679075762),
 (5644, 0.0037944123851882954),
 (5645, 0.002868420810955812),
 (5646, 0.002868420810955812),
 (5647, 0.0022193132860964726),
 (5648, 0.017210524865734874),
 (5649, 0.002868420810955812),
 (5650, 0.0011096566430482363),
 (5651, 0.0006491075248593397),
 (5652, 0.003328969929144709),
 (5653, 0.002868420810955812),
 (5654, 0.002868420810955812),
 (5655, 0.005736841621911624),
 (5656, 0.04748663253350456),
 (5657, 0.002868420810955812),
 (5658, 0.029898990854428795),
 (5659, 0.008793820839537881),
 (5660, 0.009340092025078881),
 (5661, 0.002868420810955812),
 (5662, 0.002868420810955812),
 

 (5898, 0.014342104054779061),
 (5899, 0.002868420810955812),
 (5900, 0.005736841621911624),
 (5901, 0.002868420810955812),
 (5902, 0.005736841621911624),
 (5904, 0.002868420810955812),
 (5905, 0.0011096566430482363),
 (5906, 0.0006491075248593397),
 (5907, 0.0022193132860964726),
 (5908, 0.002868420810955812),
 (5909, 0.002868420810955812),
 (5910, 0.0035175283358151524),
 (5911, 0.014425536359627072),
 (5912, 0.002868420810955812),
 (5913, 0.002868420810955812),
 (5914, 0.002868420810955812),
 (5915, 0.013315879716578835),
 (5916, 0.0011675115031348601),
 (5917, 0.0011096566430482363),
 (5918, 0.005736841621911624),
 (5919, 0.0011096566430482363),
 (5920, 0.007035056671630305),
 (5921, 0.0012982150497186794),
 (5922, 0.011473683243823248),
 (5923, 0.0005837557515674301),
 (5924, 0.005548283215241182),
 (5925, 0.002868420810955812),
 (5926, 0.0026269008820534357),
 (5927, 0.0011096566430482363),
 (5928, 0.0011096566430482363),
 (5929, 0.003894645149156038),
 (5930, 0.01407011334326061

 (6172, 0.04589473297529299),
 (6173, 0.10039472838345342),
 (6174, 0.002868420810955812),
 (6175, 0.014342104054779061),
 (6176, 0.005736841621911624),
 (6177, 0.005736841621911624),
 (6178, 0.002868420810955812),
 (6179, 0.008605262432867437),
 (6180, 0.002868420810955812),
 (6181, 0.002868420810955812),
 (6182, 0.002868420810955812),
 (6183, 0.15202630298065806),
 (6184, 0.17784209027926035),
 (6185, 0.022947366487646496),
 (6186, 0.005736841621911624),
 (6187, 0.002868420810955812),
 (6188, 0.002868420810955812),
 (6189, 0.005736841621911624),
 (6190, 0.002868420810955812),
 (6191, 0.002868420810955812),
 (6192, 0.002868420810955812),
 (6193, 0.005736841621911624),
 (6194, 0.002868420810955812),
 (6195, 0.002868420810955812),
 (6196, 0.002868420810955812),
 (6197, 0.002868420810955812),
 (6198, 0.005736841621911624),
 (6199, 0.002868420810955812),
 (6200, 0.011473683243823248),
 (6201, 0.002868420810955812),
 (6202, 0.002868420810955812),
 (6203, 0.002868420810955812),
 (6204, 0.00

In [21]:
lda_model = gensim.models.LdaMulticore(bow_corpus, num_topics=10, id2word=dictionary, passes=1, workers=2)

In [24]:
for idx, topic in lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.015*"male" + 0.011*"femal" + 0.010*"differ" + 0.009*"speci" + 0.008*"colour" + 0.006*"case" + 0.006*"sex" + 0.005*"bird" + 0.005*"sexual" + 0.004*"form"
Topic: 1 
Words: 0.008*"male" + 0.006*"femal" + 0.005*"speci" + 0.005*"say" + 0.005*"differ" + 0.004*"colour" + 0.004*"case" + 0.004*"arcot" + 0.004*"know" + 0.004*"come"
Topic: 2 
Words: 0.009*"male" + 0.006*"femal" + 0.006*"speci" + 0.005*"differ" + 0.005*"colour" + 0.005*"form" + 0.004*"case" + 0.004*"sex" + 0.003*"time" + 0.003*"say"
Topic: 3 
Words: 0.012*"male" + 0.008*"differ" + 0.007*"femal" + 0.006*"colour" + 0.004*"speci" + 0.004*"bird" + 0.004*"anim" + 0.004*"like" + 0.004*"say" + 0.004*"sex"
Topic: 4 
Words: 0.010*"male" + 0.008*"femal" + 0.007*"colour" + 0.007*"differ" + 0.006*"speci" + 0.005*"bird" + 0.004*"form" + 0.004*"say" + 0.003*"charact" + 0.003*"sex"
Topic: 5 
Words: 0.010*"male" + 0.007*"femal" + 0.006*"differ" + 0.006*"speci" + 0.005*"form" + 0.005*"colour" + 0.004*"bird" + 0.004*"sex" + 0.004

In [25]:
lda_model_tfidf = gensim.models.LdaMulticore(corpus_tfidf, num_topics=10, id2word=dictionary, passes=2, workers=4)

In [26]:
for idx, topic in lda_model_tfidf.print_topics(-1):
    print('Topic: {} Word: {}'.format(idx, topic))

Topic: 0 Word: 0.000*"ebook" + 0.000*"ernst" + 0.000*"gutenberg" + 0.000*"html" + 0.000*"header" + 0.000*"haeckel" + 0.000*"asscher" + 0.000*"derek" + 0.000*"midnight" + 0.000*"ibiblio"
Topic: 1 Word: 0.000*"arcot" + 0.000*"ebook" + 0.000*"morey" + 0.000*"gutenberg" + 0.000*"ernst" + 0.000*"wade" + 0.000*"asscher" + 0.000*"cavor" + 0.000*"html" + 0.000*"torlo"
Topic: 2 Word: 0.000*"economist" + 0.000*"brexit" + 0.000*"polit" + 0.000*"ﬁrst" + 0.000*"aramco" + 0.000*"trump" + 0.000*"ﬁrms" + 0.000*"saudi" + 0.000*"voter" + 0.000*"minist"
Topic: 3 Word: 0.000*"speci" + 0.000*"variat" + 0.000*"femal" + 0.000*"colour" + 0.000*"intermedi" + 0.000*"male" + 0.000*"breed" + 0.000*"pigment" + 0.000*"differenti" + 0.000*"phenomena"
Topic: 4 Word: 0.001*"arcot" + 0.001*"cavor" + 0.000*"selenit" + 0.000*"morey" + 0.000*"wade" + 0.000*"torlo" + 0.000*"ship" + 0.000*"sphere" + 0.000*"moon" + 0.000*"say"
Topic: 5 Word: 0.000*"male" + 0.000*"femal" + 0.000*"sex" + 0.000*"colour" + 0.000*"sexual" + 0.000

In [27]:
processed_docs[2]

['project',
 'gutenberg',
 'ebook',
 'moon',
 'well',
 'ebook',
 'cost',
 'restrict',
 'whatsoev',
 'copi',
 'away',
 'term',
 'project',
 'gutenberg',
 'licens',
 'includ',
 'ebook',
 'onlin',
 'gutenberg',
 'titl',
 'moon',
 'author',
 'well',
 'releas',
 'date',
 'octob',
 'ebook',
 'updat',
 'juli',
 'languag',
 'english',
 'start',
 'project',
 'gutenberg',
 'ebook',
 'moon',
 'project',
 'gutenberg',
 'etext',
 'prepar',
 'barri',
 'haworth',
 'moon',
 'well',
 'chapter',
 'bedford',
 'meet',
 'cavor',
 'lympn',
 'write',
 'amidst',
 'shadow',
 'vine',
 'leav',
 'blue',
 'southern',
 'itali',
 'come',
 'certain',
 'qualiti',
 'astonish',
 'particip',
 'amaz',
 'adventur',
 'cavor',
 'outcom',
 'purest',
 'accid',
 'fell',
 'thing',
 'time',
 'think',
 'remov',
 'slightest',
 'possibl',
 'disturb',
 'experi',
 'go',
 'lympn',
 'imagin',
 'unev',
 'place',
 'world',
 'rate',
 'say',
 'shall',
 'peac',
 'chanc',
 'work',
 'book',
 'sequel',
 'utter',
 'varianc',
 'destini',
 'littl'

In [28]:
for index, score in sorted(lda_model[bow_corpus[1]], key=lambda tup: -1*tup[1]):
    print("\nScore: {}\t \nTopic: {}".format(score, lda_model.print_topic(index, 10)))


Score: 0.9988711476325989	 
Topic: 0.015*"male" + 0.011*"femal" + 0.010*"differ" + 0.009*"speci" + 0.008*"colour" + 0.006*"case" + 0.006*"sex" + 0.005*"bird" + 0.005*"sexual" + 0.004*"form"


In [29]:
for index, score in sorted(lda_model_tfidf[bow_corpus[2]], key=lambda tup: -1*tup[1]):
    print("\nScore: {}\t \nTopic: {}".format(score, lda_model_tfidf.print_topic(index, 10)))


Score: 0.9743684530258179	 
Topic: 0.001*"arcot" + 0.001*"cavor" + 0.000*"selenit" + 0.000*"morey" + 0.000*"wade" + 0.000*"torlo" + 0.000*"ship" + 0.000*"sphere" + 0.000*"moon" + 0.000*"say"

Score: 0.022432474419474602	 
Topic: 0.000*"ebook" + 0.000*"ernst" + 0.000*"gutenberg" + 0.000*"html" + 0.000*"header" + 0.000*"haeckel" + 0.000*"asscher" + 0.000*"derek" + 0.000*"midnight" + 0.000*"ibiblio"


In [30]:
test_file = open('Democracy in America.txt','r')
test_file_text = test_file.read()
test_file.close()

tokens = test_file_text.split()
vocab = list(set(tokens))

unseen_document = test_file_text
bow_vector = dictionary.doc2bow(preprocess(unseen_document))

for index, score in sorted(lda_model[bow_vector], key=lambda tup: -1*tup[1]):
    print("Score: {}\t Topic: {}".format(score, lda_model.print_topic(index, 5)))

Score: 0.2765149176120758	 Topic: 0.011*"male" + 0.010*"femal" + 0.007*"colour" + 0.004*"differ" + 0.004*"speci"
Score: 0.24740447103977203	 Topic: 0.008*"male" + 0.006*"femal" + 0.005*"speci" + 0.005*"say" + 0.005*"differ"
Score: 0.19391782581806183	 Topic: 0.010*"male" + 0.008*"femal" + 0.007*"colour" + 0.007*"differ" + 0.006*"speci"
Score: 0.12378450483083725	 Topic: 0.009*"male" + 0.009*"femal" + 0.006*"colour" + 0.005*"speci" + 0.005*"case"
Score: 0.0821586474776268	 Topic: 0.015*"male" + 0.011*"femal" + 0.010*"differ" + 0.009*"speci" + 0.008*"colour"
Score: 0.03690759465098381	 Topic: 0.010*"male" + 0.007*"femal" + 0.006*"differ" + 0.006*"speci" + 0.005*"form"
Score: 0.017821181565523148	 Topic: 0.009*"male" + 0.007*"femal" + 0.005*"differ" + 0.004*"speci" + 0.004*"case"
Score: 0.01691647619009018	 Topic: 0.012*"male" + 0.008*"differ" + 0.007*"femal" + 0.006*"colour" + 0.004*"speci"


In [31]:
print('\nPerplexity: ', lda_model.log_perplexity(bow_corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=processed_docs, dictionary=dictionary, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -8.598385679209368

Coherence Score:  0.37675070977806047


In [33]:
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, bow_corpus, dictionary,  mds='mmds')

C:\Users\SK\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


In [34]:
pyLDAvis.display(vis)

In [36]:
list_books = ['The-Economist-USA.txt','The_Descent_of_Man.txt','Problems of Genetics.txt']
file = [open(book,'r', encoding="utf8") for book in list_books]

file_text = [fil.read() for fil in file]
df_text = pd.DataFrame(file_text)
df_text['index'] = df_text.index
documents = df_text
for fil in file:
    fil.close()

In [37]:
stemmer = SnowballStemmer('english')

def lemmatize_stemming(text):
    return stemmer.stem(WordNetLemmatizer().lemmatize(text, pos='v'))

def preprocess(text):
    result = []
    for token in gensim.utils.simple_preprocess(text):
        if token not in gensim.parsing.preprocessing.STOPWORDS and len(token) > 3:
            result.append(lemmatize_stemming(token))
    return result

In [38]:
doc_sample = documents[documents['index'] == 1].values[0][0]

print('\n\n tokenized and lemmatized document: ')
print(preprocess(doc_sample))




 tokenized and lemmatized document: 


['project', 'gutenberg', 'ebook', 'descent', 'charl', 'darwin', 'ebook', 'cost', 'restrict', 'whatsoev', 'copi', 'away', 'term', 'project', 'gutenberg', 'licens', 'includ', 'ebook', 'onlin', 'gutenberg', 'titl', 'descent', 'author', 'charl', 'darwin', 'post', 'date', 'januari', 'ebook', 'post', 'novemb', 'updat', 'octob', 'languag', 'english', 'start', 'project', 'gutenberg', 'ebook', 'descent', 'produc', 'asscher', 'descent', 'select', 'relat', 'work', 'charl', 'darwin', 'life', 'letter', 'charl', 'darwin', 'chapter', 'edit', 'franci', 'darwin', 'portrait', 'volum', 'popular', 'edit', 'condens', 'volum', 'naturalist', 'journal', 'research', 'natur', 'histori', 'geolog', 'countri', 'visit', 'voyag', 'round', 'world', 'illustr', 'pritchett', 'popular', 'edit', 'woodcut', 'cheaper', 'edit', 'origin', 'speci', 'mean', 'natur', 'select', 'preserv', 'favour', 'race', 'struggl', 'life', 'larg', 'type', 'edit', 'volum', 'popular', 'edit', 'cheaper', 'edit', 'portrait', 'contriv', 'orchid', 'f

In [39]:
dictionary = gensim.corpora.Dictionary(processed_docs)

In [40]:
bow_corpus = [dictionary.doc2bow(doc) for doc in processed_docs]
print(len(bow_corpus))
bow_corpus[1]

6


[(1, 1),
 (10, 7),
 (12, 83),
 (13, 2),
 (15, 26),
 (17, 2),
 (18, 5),
 (21, 2),
 (22, 76),
 (23, 30),
 (24, 7),
 (25, 4),
 (26, 2),
 (27, 10),
 (30, 12),
 (32, 2),
 (34, 45),
 (35, 14),
 (36, 8),
 (37, 13),
 (39, 15),
 (41, 193),
 (42, 163),
 (43, 1),
 (44, 3),
 (46, 7),
 (48, 1),
 (49, 312),
 (50, 11),
 (53, 53),
 (54, 159),
 (55, 39),
 (58, 1),
 (59, 54),
 (60, 8),
 (61, 8),
 (63, 58),
 (64, 63),
 (66, 40),
 (67, 10),
 (76, 105),
 (77, 3),
 (78, 127),
 (80, 10),
 (83, 259),
 (86, 80),
 (87, 91),
 (88, 3),
 (89, 4),
 (92, 2),
 (93, 3),
 (95, 4),
 (97, 14),
 (98, 46),
 (99, 1),
 (100, 2),
 (101, 101),
 (102, 49),
 (103, 1),
 (104, 56),
 (105, 32),
 (107, 5),
 (110, 3),
 (111, 7),
 (113, 33),
 (114, 28),
 (116, 1),
 (120, 28),
 (121, 1),
 (132, 7),
 (141, 1),
 (142, 6),
 (145, 2),
 (151, 1),
 (152, 6),
 (153, 56),
 (154, 10),
 (163, 124),
 (164, 4),
 (165, 5),
 (167, 17),
 (174, 23),
 (175, 9),
 (178, 21),
 (182, 13),
 (183, 2),
 (184, 1),
 (191, 118),
 (192, 154),
 (196, 1),
 (198, 4)

In [41]:
lda_model = gensim.models.LdaMulticore(bow_corpus, num_topics=20, id2word=dictionary, passes=1, workers=2)

In [42]:
for idx, topic in lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.014*"male" + 0.008*"femal" + 0.005*"colour" + 0.005*"speci" + 0.005*"differ" + 0.004*"form" + 0.004*"case" + 0.004*"bird" + 0.004*"come" + 0.004*"natur"
Topic: 1 
Words: 0.005*"femal" + 0.005*"male" + 0.004*"say" + 0.004*"work" + 0.004*"arcot" + 0.004*"form" + 0.004*"power" + 0.003*"case" + 0.003*"come" + 0.003*"ship"
Topic: 2 
Words: 0.014*"male" + 0.012*"femal" + 0.008*"differ" + 0.005*"bird" + 0.005*"colour" + 0.005*"speci" + 0.005*"sex" + 0.004*"anim" + 0.003*"charact" + 0.003*"probabl"
Topic: 3 
Words: 0.013*"male" + 0.009*"femal" + 0.007*"differ" + 0.007*"colour" + 0.006*"speci" + 0.005*"bird" + 0.005*"sex" + 0.005*"anim" + 0.004*"case" + 0.004*"like"
Topic: 4 
Words: 0.013*"male" + 0.012*"femal" + 0.007*"differ" + 0.007*"colour" + 0.006*"bird" + 0.006*"speci" + 0.005*"case" + 0.005*"anim" + 0.005*"sex" + 0.004*"sexual"
Topic: 5 
Words: 0.009*"femal" + 0.009*"male" + 0.007*"differ" + 0.005*"colour" + 0.004*"speci" + 0.004*"say" + 0.004*"know" + 0.004*"bird" + 0

In [43]:
for index, score in sorted(lda_model[bow_corpus[1]], key=lambda tup: -1*tup[1]):
    print("\nScore: {}\t \nTopic: {}".format(score, lda_model.print_topic(index, 10)))


Score: 0.3536083996295929	 
Topic: 0.012*"male" + 0.012*"femal" + 0.009*"speci" + 0.008*"differ" + 0.007*"colour" + 0.006*"sex" + 0.005*"bird" + 0.004*"case" + 0.004*"anim" + 0.004*"great"

Score: 0.3498832583427429	 
Topic: 0.013*"male" + 0.012*"femal" + 0.007*"differ" + 0.007*"colour" + 0.006*"bird" + 0.006*"speci" + 0.005*"case" + 0.005*"anim" + 0.005*"sex" + 0.004*"sexual"

Score: 0.293453186750412	 
Topic: 0.018*"male" + 0.011*"colour" + 0.010*"femal" + 0.009*"differ" + 0.007*"case" + 0.006*"speci" + 0.006*"sex" + 0.006*"bird" + 0.005*"anim" + 0.005*"sexual"


In [44]:
print('\nPerplexity: ', lda_model.log_perplexity(bow_corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=processed_docs, dictionary=dictionary, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -9.346355973021442

Coherence Score:  0.3599786976498738


In [46]:
test_file = open('The Last Evolution.txt','r')
test_file_text = test_file.read()
test_file.close()

tokens = test_file_text.split()
vocab = list(set(tokens))

unseen_document = test_file_text
bow_vector = dictionary.doc2bow(preprocess(unseen_document))

for index, score in sorted(lda_model[bow_vector], key=lambda tup: -1*tup[1]):
    print("Score: {}\t Topic: {}".format(score, lda_model.print_topic(index, 5)))

Score: 0.37628817558288574	 Topic: 0.007*"form" + 0.006*"male" + 0.006*"femal" + 0.006*"differ" + 0.005*"colour"
Score: 0.36085566878318787	 Topic: 0.008*"male" + 0.006*"say" + 0.005*"colour" + 0.005*"femal" + 0.005*"speci"
Score: 0.1585923284292221	 Topic: 0.006*"differ" + 0.006*"male" + 0.005*"speci" + 0.005*"form" + 0.005*"femal"
Score: 0.06490256637334824	 Topic: 0.009*"male" + 0.006*"femal" + 0.005*"colour" + 0.005*"come" + 0.005*"like"
Score: 0.013996445573866367	 Topic: 0.008*"male" + 0.006*"differ" + 0.005*"colour" + 0.005*"femal" + 0.005*"bird"
Score: 0.010114007629454136	 Topic: 0.005*"male" + 0.005*"say" + 0.004*"femal" + 0.004*"speci" + 0.004*"differ"


In [47]:
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, bow_corpus, dictionary, mds='mmds')

C:\Users\SK\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


In [48]:
pyLDAvis.display(vis)